In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error,mean_absolute_error
from sklearn.model_selection import TimeSeriesSplit, cross_val_predict, KFold, cross_val_score
import os
import json
from glob import glob
from sklearn.base import clone
import optuna
import lightgbm as lgb
import xgboost as xgb
from sklearn.svm import SVR
from sklearn.linear_model import BayesianRidge

# Load flower data

In [2]:
file_list = ['kyoto', 'liestal', 'nyc', 'washingtondc', 'vancouver']
df_list = []

for file_name in file_list:
    df_list.append(pd.read_csv(f"data/{file_name}.csv"))

df = pd.concat(df_list, ignore_index=True)

The historic data includes a dummy row for the year 2025. We included this row to make the feature engineering easier. 

# Weather data

From past competitions, we already know that incorporating weather data into our forecasting models significantly improves accuracy. Therefore, we collected historical weather data for various locations, along with weather forecasts for the month of March, to enhance our model with this additional information.

In [3]:
def process_weather_data_with_advanced_features(folder_path):
    """
    Processes multiple weather CSV files and extracts key features for bloom prediction:
    - Growing Degree Days (GDD) from Jan to March
    - Warm Spell Days (>15°C in Feb-March)
    - Temperature Trend (Mean & Std Dev from Jan to March)
    - Temperature Variability (Nov–Jan)
    - Cold Days (<10°C)
    
    Args:
    folder_path (str): Path to the folder containing weather CSV files.

    Returns:
    pd.DataFrame: Concatenated DataFrame with processed weather data for all locations.
    """

    all_files = glob(os.path.join(folder_path, "*.csv"))
    processed_data = []

    for file in all_files:
        # Extract location name from filename
        location_name = os.path.basename(file).replace("_weather", "").replace("_", "/").replace(".csv", "")
        if location_name.lower() == "nyc":
            location_name = "newyorkcity"

        # Load and process weather data
        df_weather = pd.read_csv(file)
        df_weather["date"] = pd.to_datetime(df_weather["date"])

        # Extract year, month, and DOY
        df_weather["year"] = df_weather["date"].dt.year
        df_weather["month"] = df_weather["date"].dt.month
        df_weather["DOY"] = df_weather["date"].dt.dayofyear

        # Identify leap years
        df_weather["leap_year"] = df_weather["year"].apply(lambda x: 1 if (x % 4 == 0 and x % 100 != 0) or (x % 400 == 0) else 0)

        # Filter for relevant months (October to March)
        df_weather_filtered = df_weather[df_weather["month"].isin([10, 11, 12, 1, 2])].copy()

        # Shift October-December to the next year for bloom alignment
        df_weather_filtered.loc[df_weather_filtered["month"].isin([10, 11, 12]), "year"] += 1

        # Compute daily averages
        df_daily_means = df_weather_filtered.groupby(["year", "DOY"]).agg({
            "temperature_2m_max": "mean",
            "temperature_2m_mean": "mean",
            "temperature_2m_min": "mean",
            "precipitation_sum": "mean",
            "rain_sum": "mean"
        }).reset_index()

        # Compute count of cold days separately
        df_cold_days = df_weather_filtered.groupby(["year", "DOY"])["temperature_2m_mean"].apply(lambda x: (x < 10).sum()).reset_index()
        df_cold_days.rename(columns={"temperature_2m_mean": "cold_days_below_10"}, inplace=True)

        # Compute temperature variability (std dev) for Nov-Jan per year-month
        df_temp_variability = df_weather_filtered[df_weather_filtered["month"].isin([11, 12, 1,2])].groupby(["year", "month"]).agg({
            "temperature_2m_mean": "std"
        }).reset_index().rename(columns={"temperature_2m_mean": "temp_variability"})

        # Feature 1: Growing Degree Days (GDD) - Base Temp 5°C (Jan-Mar)
        df_weather_filtered["GDD"] = df_weather_filtered["temperature_2m_mean"].apply(lambda x: max(0, x - 5))
        df_GDD = df_weather_filtered[df_weather_filtered["month"].isin([1, 2])].groupby("year")["GDD"].sum().reset_index().rename(columns={"GDD": "total_GDD_Jan_Mar"})

        # Feature 2: Warm Spell Detection (Days > 15°C in Feb-March)
        df_weather_filtered["warm_spell_day"] = df_weather_filtered["temperature_2m_mean"] > 15
        df_warm_spells = df_weather_filtered[df_weather_filtered["month"].isin([1,2])].groupby("year")["warm_spell_day"].sum().reset_index().rename(columns={"warm_spell_day": "total_warm_spells_Feb_Mar"})

        # Feature 3: Temperature Trend (Mean & Std from Jan to March)
        temp_trend = df_weather_filtered[df_weather_filtered["month"].isin([1, 2])].groupby("year").agg({"temperature_2m_mean": ["mean", "std"]})
        temp_trend.columns = ["temp_trend_mean", "temp_trend_std"]
        temp_trend.reset_index(inplace=True)

        # Merge cold day counts into daily means
        df_daily_means = df_daily_means.merge(df_cold_days, on=["year", "DOY"], how="left")

        # Ensure every (year, DOY) combination exists
        all_years = df_weather_filtered["year"].unique()
        valid_doys = df_weather_filtered["DOY"].unique()  # Only DOYs for Oct-Apr
        all_doys = sorted(valid_doys)  # Sort to maintain order

        full_doy_grid = pd.MultiIndex.from_product(
            [all_years, all_doys],
            names=["year", "DOY"]
        ).to_frame(index=False)

        # Merge to enforce a uniform structure
        df_daily_means_full = full_doy_grid.merge(df_daily_means, on=["year", "DOY"], how="left")

        # Fill missing values robustly
        df_daily_means_full.interpolate(method="linear", inplace=True)  # Fill using trends
        df_daily_means_full.fillna(df_daily_means_full.groupby("DOY").transform("median"), inplace=True)  # Use median where gaps exist
        df_daily_means_full.fillna(0, inplace=True)  # Ensure no NaNs remain

        # Add leap year column
        df_daily_means_full["leap_year"] = df_daily_means_full["year"].apply(lambda x: 1 if (x % 4 == 0 and x % 100 != 0) or (x % 400 == 0) else 0)

        # Pivot into a structured dataset (one row per year, columns per DOY)
        df_pivot_doy = df_daily_means_full.pivot(index="year", columns="DOY", values=["temperature_2m_max", "temperature_2m_mean", "temperature_2m_min", "precipitation_sum", "rain_sum", "cold_days_below_10"])

        # Flatten column names
        df_pivot_doy.columns = [f"{var}_DOY{doy}" for var, doy in df_pivot_doy.columns]

        # Reset index to keep "year" as a column
        df_pivot_doy.reset_index(inplace=True)

        # Add location column
        df_pivot_doy["location"] = location_name

        # Merge additional climate features
        df_additional_features = df_GDD.merge(df_warm_spells, on="year").merge(temp_trend, on="year")
        df_pivot_doy = df_pivot_doy.merge(df_additional_features, on="year", how="left")

        # Merge temperature variability per year-month into the dataset
        df_temp_variability_pivot = df_temp_variability.pivot(index="year", columns="month", values="temp_variability")
        df_temp_variability_pivot.columns = [f"temp_variability_M{month}" for month in df_temp_variability_pivot.columns]

        # Merge temperature variability into the final dataset
        df_pivot_doy = df_pivot_doy.merge(df_temp_variability_pivot, on="year", how="left")

        # Append to list
        processed_data.append(df_pivot_doy)

    # Concatenate all locations into a single dataframe
    final_df = pd.concat(processed_data, ignore_index=True)

    return final_df



processed_weather_data = process_weather_data_with_advanced_features("weather/")


# Additional information: 

We focus only on data from 1980 onward, as a key study on regime shifts in flowering data (https://www.researchgate.net/publication/284484997_Global_impacts_of_the_1980s_regime_shift) highlighted a significant change around that time. Building on this, we also found that using historical data before 2000 leads to significantly worse predictions for more recent years (2022 and beyond). Therefore, we exclude all data points prior to 2000.

Additionally, we incorporate non-linear features such as the squared year to account for the acceleration effect of global warming. We also include transformations like log(year) and interactions such as year * latitude.

Finally, we enhance our model with rolling values of the peak flowering date to capture temporal trends more effectively.

In [4]:
# Ensure only necessary columns exist
df_training = df[['year', 'location', 'bloom_doy', 'alt', 'lat', 'long']].dropna()


# Convert year to numeric
df_training['year'] = pd.to_numeric(df_training['year'], errors='coerce')
df_training['year_squared'] = df_training['year'] ** 2
df_training['log_year'] = np.log(df_training['year'])
# df_training['year_lat_long'] = df_training['year'] * df_training['lat']*df_training['long']
df_training['year_alt'] = df_training['year'] * df_training['alt']


# Sort data by location and year for< rolling calculations
df_training = df_training.sort_values(by=['location', 'year'])

# Compute rolling averages for bloom_doy within each location
df_training['bloom_doy_lag1'] = df_training.groupby('location')['bloom_doy'].shift(1)  # Last year's bloom day
df_training['bloom_doy_rolling2'] = df_training.groupby('location')['bloom_doy'].shift(1).rolling(window=2, min_periods=1).mean()
df_training['bloom_doy_rolling3'] = df_training.groupby('location')['bloom_doy'].shift(1).rolling(window=3, min_periods=1).mean()  
df_training['bloom_doy_rolling4'] = df_training.groupby('location')['bloom_doy'].shift(1).rolling(window=4, min_periods=1).mean()
df_training['bloom_doy_rolling5'] = df_training.groupby('location')['bloom_doy'].shift(1).rolling(window=5, min_periods=1).mean()  
df_training['bloom_doy_rolling7'] = df_training.groupby('location')['bloom_doy'].shift(1).rolling(window=7, min_periods=1).mean() 
df_training['bloom_doy_rolling10'] = df_training.groupby('location')['bloom_doy'].shift(1).rolling(window=10, min_periods=1).mean() 
df_training['alt_year'] = df_training['year']*df_training['alt']

df_training = df_training[df_training['year']>= 2000]

nyc_mask = (df_training['location'] == 'newyorkcity') & (df_training['year'] >= 2024)


df_training.loc[nyc_mask, 'bloom_doy_lag1'] = df_training.loc[nyc_mask, 'bloom_doy']


df_training.loc[nyc_mask, 'bloom_doy_rolling2'] =  df_training.loc[nyc_mask, 'bloom_doy']


df_training.loc[nyc_mask, 'bloom_doy_rolling3'] =  df_training.loc[nyc_mask, 'bloom_doy']

df_training.loc[nyc_mask, 'bloom_doy_rolling4'] =  df_training.loc[nyc_mask, 'bloom_doy']


df_training.loc[nyc_mask, 'bloom_doy_rolling5'] =  df_training.loc[nyc_mask, 'bloom_doy']


df_training.loc[nyc_mask, 'bloom_doy_rolling7'] = df_training.loc[nyc_mask, 'bloom_doy']


df_training.loc[nyc_mask, 'bloom_doy_rolling10'] =  df_training.loc[nyc_mask, 'bloom_doy']

# Merge the flower data with the weather data
df_training = df_training.merge(processed_weather_data, on=["year", "location"], how="left")

In [5]:
df_training[df_training['year']>=2025]

year      location  bloom_doy    alt        lat        long  year_squared  \
25  2025         kyoto         95   44.0  35.011983  135.676114       4100625   
51  2025       liestal         80  350.0  47.481400    7.730519       4100625   
53  2025   newyorkcity         88    8.5  40.730400  -73.998090       4100625   
57  2025     vancouver         83   24.0  49.223700 -123.163600       4100625   
83  2025  washingtondc         77    0.0  38.885350  -77.038628       4100625   

    log_year  year_alt  bloom_doy_lag1  ...  cold_days_below_10_DOY365  \
25  7.613325   89100.0            95.0  ...                        1.0   
51  7.613325  708750.0            80.0  ...                        1.0   
53  7.613325   17212.5            88.0  ...                        0.0   
57  7.613325   48600.0            83.0  ...                        1.0   
83  7.613325       0.0            77.0  ...                        0.0   

    cold_days_below_10_DOY366  total_GDD_Jan_Mar  total_warm_spells_Feb_Mar  \
25                        1.0          17.319431                          0   
51                        1.0          54.360581                          0   
53                        1.0          12.738154                          0   
57                        1.0          32.928411                          0   
83                        1.0          36.983739                          0   

    temp_trend_mean  temp_trend_std  temp_variability_M1  temp_variability_M2  \
25         3.354087        2.178515             1.523789             2.706559   
51         3.570207        3.496741             3.730996             3.265215   
53        -0.860972        4.319810             4.333032             4.008815   
57         2.686385        3.773514             1.584476             5.197577   
83         0.703046        5.087352             4.593043             4.620523   

    temp_variability_M11  temp_variability_M12  
25              3.566410              1.999722  
51              3.430981              2.550234  
53              4.944797              5.644917  
57              2.337159              1.745614  
83              5.028049              4.842168  

[5 rows x 943 columns]

The additional features we created also introduced noise into our dataset. Having too many irrelevant features can negatively impact our model’s accuracy by adding unnecessary complexity.

To maintain clarity in this notebook, we do not include the feature selection code. However, after careful evaluation, we finalized a set of 191 features. These were selected based on feature importance rankings from a LightGBM model, ensuring that only the most relevant predictors were retained.

In [6]:
# 1. Prepare the data
# Create dummy variables for 'location' and filter for years < 2024
df_training_dummies = pd.get_dummies(df_training, columns=['location'], drop_first=True).dropna()
df_training_dummies['washington_year']= df_training_dummies['year']*df_training_dummies['log_year']
df_training_dummies_filter = df_training_dummies[df_training_dummies['year'] < 2024]

# Separate features and target
X = df_training_dummies_filter.drop(columns=['bloom_doy'])
y = df_training_dummies_filter['bloom_doy']

# 2. Optionally, scale numerical features

scaler = StandardScaler()
X_scaled_arr = scaler.fit_transform(X)
# Convert back to DataFrame to retain column names
X_scaled = pd.DataFrame(X_scaled_arr, columns=X.columns, index=X.index)

# 3. Evaluate a LightGBM model using TimeSeriesSplit CV
tscv = TimeSeriesSplit(n_splits=5)
rmse_list = []

print("Evaluating LightGBM model with TimeSeriesSplit:")
for fold, (train_idx, test_idx) in enumerate(tscv.split(X_scaled), start=1):
    X_train, X_test = X_scaled.iloc[train_idx], X_scaled.iloc[test_idx]
    y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
    
    # Define and train the LightGBM regressor
    model = lgb.LGBMRegressor(random_state=42, verbosity = -1)
    model.fit(X_train, y_train,
              eval_set=[(X_test, y_test)])
    
    y_pred = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    rmse_list.append(rmse)
    print(f"Fold {fold} RMSE: {rmse:.2f}")

print(f"\nAverage RMSE from LightGBM (all features): {np.mean(rmse_list):.2f}\n")

# 4. Train a final LightGBM model on all training data to extract feature importances
final_model = lgb.LGBMRegressor(random_state=42, verbosity = -1)
final_model.fit(X_scaled, y)
feature_importances = final_model.feature_importances_


feat_imp_df = pd.DataFrame({'feature': X_scaled.columns, 'importance': feature_importances})
feat_imp_df = feat_imp_df.sort_values(by='importance', ascending=False)

Evaluating LightGBM model with TimeSeriesSplit:
Fold 1 RMSE: 6.26
Fold 2 RMSE: 7.70
Fold 3 RMSE: 8.88
Fold 4 RMSE: 6.29
Fold 5 RMSE: 7.49

Average RMSE from LightGBM (all features): 7.32



# Hyperparameter tuning

We began our model selection process with four candidates: LightGBM, XGBoost, SVR, and Bayesian Ridge regression. To achieve optimal performance, we tuned their hyperparameters.

The code block below performs this tuning automatically. However, to streamline the workflow, we have already saved the optimized hyperparameters in a JSON file.

In [7]:
selected_features =  feat_imp_df.head(191)['feature'].tolist()

In [ ]:
# def tune_model_with_optuna(model_name: str,
#                            X_train: np.ndarray, y_train: np.ndarray,
#                            X_test: np.ndarray, y_test: np.ndarray,
#                            n_trials: int = 50) -> dict:
#     """
#     Tune hyperparameters for a given model using Optuna with a fixed train-test split.
#     Returns the best hyperparameters.
#     """
#     def objective(trial: optuna.Trial) -> float:
#         if model_name == "SVR":
#             params = {
#                 "C": trial.suggest_float("C", 0.1, 1.0, log=True),
#                 "epsilon": trial.suggest_float("epsilon", 0.01, 1.0),
#                 "kernel": trial.suggest_categorical("kernel", ["linear"]),
#             }
#             model = SVR(**params)
            
#         elif model_name == "BayesianRidge":
#             params = {
#                 "alpha_1": trial.suggest_float("alpha_1", 1e-6, 1e-2, log=True),
#                 "alpha_2": trial.suggest_float("alpha_2", 1e-6, 1e-2, log=True),
#                 "lambda_1": trial.suggest_float("lambda_1", 1e-6, 1e-2, log=True),
#                 "lambda_2": trial.suggest_float("lambda_2", 1e-6, 1e-2, log=True),
#             }
#             model = BayesianRidge(**params)
            
#         elif model_name == "LightGBM":
#             params = {
#                 "objective": "regression",
#                 "metric": "rmse",
#                 "verbosity": -1,
#                 "boosting_type": "gbdt",
#                 "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
#                 "num_leaves": trial.suggest_int("num_leaves", 20, 150),
#                 "max_depth": trial.suggest_int("max_depth", 3, 15),
#                 "min_child_samples": trial.suggest_int("min_child_samples", 5, 50),
#                 "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 10),
#                 "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 10),
#                 "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 0.9), 
#                 "n_estimators": trial.suggest_int("n_estimators", 250, 600, step=25)
#             }
#             model = lgb.LGBMRegressor(**params)
            
#         elif model_name == "XGBoost":
#             params = {
#                 "n_estimators": trial.suggest_int("n_estimators", 250, 600, step=25),
#                 "max_depth": trial.suggest_int("max_depth", 1, 20),
#                 "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
#                 "gamma": trial.suggest_float("gamma", 0, 5),
#                 "min_child_weight": trial.suggest_int("min_child_weight", 1, 30),
#                 "subsample": trial.suggest_float("subsample", 0.5, 0.9),
#                 "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 0.9),
#                 "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 10, log=True),
#                 "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 10, log=True)
#             }
#             model = xgb.XGBRegressor(**params)
      
            
#         else:
#             return float("inf")
        
#         # Train on the fixed training set and evaluate on the fixed test set.
#         model.fit(X_train, y_train)
#         y_pred = model.predict(X_test)
#         rmse = np.sqrt(np.mean((y_test - y_pred) ** 2))
#         return rmse

#     study = optuna.create_study(direction="minimize")
#     study.optimize(objective, n_trials=n_trials)
#     return study.best_params


# def tune_and_save_hyperparams(df_training: pd.DataFrame, selected_features: list,
#                               models_to_tune: list, n_trials: int = 50,
#                               save_path: str = "hyperparams_feb.json") -> dict:
#     """
#     Tunes hyperparameters for each model in models_to_tune using a fixed train-test split,
#     where the test set includes all rows with year >= 2022, and saves them to a JSON file.
#     """
#     # Split the data based on the "year" column
#     train_df = df_training[df_training["year"] < 2023]
#     test_df = df_training[df_training["year"] >= 2023]
    
#     # Select features and target variable
#     X_train = train_df[selected_features]
#     y_train = train_df["bloom_doy"]
#     X_test = test_df[selected_features]
#     y_test = test_df["bloom_doy"]
    
#     # Fit the scaler on training data and transform both sets
#     scaler = StandardScaler()
#     X_train_scaled = scaler.fit_transform(X_train)
#     X_test_scaled = scaler.transform(X_test)
    
#     hyperparams = {}
#     for model_name in models_to_tune:
#         print(f"Tuning {model_name}...")
#         best_params = tune_model_with_optuna(model_name, X_train_scaled, y_train,
#                                              X_test_scaled, y_test, n_trials)
#         print(f"Best parameters for {model_name}: {best_params}")
#         hyperparams[model_name] = best_params



#     #Save the hyperparameters to a JSON file
#     with open(save_path, "w") as f:
#         json.dump(hyperparams, f)
#     return hyperparams




# # Example usage:
# models_to_tune = ["SVR", "BayesianRidge", "LightGBM", "XGBoost"]

# # df_training_dummies_filter is your training dataframe which must contain a "year" column.
# hyperparams = tune_and_save_hyperparams(df_training_dummies, selected_features, models_to_tune, n_trials=2500)



[I 2025-02-24 21:16:27,622] A new study created in memory with name: no-name-2dbfa8ea-d663-4a53-a267-269dbdbf6771
[I 2025-02-24 21:16:27,633] Trial 0 finished with value: 5.745869563206387 and parameters: {'C': 0.10146934377109619, 'epsilon': 0.3354897045927168, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.


[I 2025-02-24 21:16:27,648] Trial 1 finished with value: 5.986654311953665 and parameters: {'C': 0.12200919805787433, 'epsilon': 0.40033993045952493, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,658] Trial 2 finished with value: 6.7009436836114755 and parameters: {'C': 0.20831733259604432, 'epsilon': 0.548448377816249, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,665] Trial 3 finished with value: 6.662683685626526 and parameters: {'C': 0.495847105195159, 'epsilon': 0.973039140376546, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,673] Trial 4 finished with value: 6.932697321371895 and parameters: {'C': 0.3939675062578306, 'epsilon': 0.666288368983188, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,683] Trial 5 finished with value: 7.000140790826467 and parameters: {'C': 0.7320483578751756, 'epsilon': 0.604852

Tuning SVR...


[I 2025-02-24 21:16:27,843] Trial 12 finished with value: 6.8717439350634 and parameters: {'C': 0.1682598895724099, 'epsilon': 0.016433953992494033, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,869] Trial 13 finished with value: 5.836745145749603 and parameters: {'C': 0.10409561868236114, 'epsilon': 0.23952332556382677, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,890] Trial 14 finished with value: 6.712887844821666 and parameters: {'C': 0.1641976486932221, 'epsilon': 0.2779477685295792, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,907] Trial 15 finished with value: 6.637110971241801 and parameters: {'C': 0.1551866194906845, 'epsilon': 0.24046021698650386, 'kernel': 'linear'}. Best is trial 0 with value: 5.745869563206387.
[I 2025-02-24 21:16:27,922] Trial 16 finished with value: 6.884810142946648 and parameters: {'C': 0.2197524747534134, 'epsilon': 

Best parameters for SVR: {'C': 0.10000954289226048, 'epsilon': 0.9996810283280949, 'kernel': 'linear'}
Tuning BayesianRidge...


...

Best parameters for BayesianRidge: {'alpha_1': 0.009967438185890574, 'alpha_2': 0.0002747338713334643, 'lambda_1': 3.847626427614395e-06, 'lambda_2': 0.009992039927281857}
Tuning LightGBM...


[I 2025-02-24 21:23:52,988] Trial 5 finished with value: 4.596679002017695 and parameters: {'learning_rate': 0.1728826101661296, 'num_leaves': 74, 'max_depth': 9, 'min_child_samples': 24, 'reg_alpha': 1.0957705398309108, 'reg_lambda': 7.332645403103445, 'colsample_bytree': 0.6302426268267106, 'n_estimators': 500}. Best is trial 3 with value: 4.2556751158162225.
[I 2025-02-24 21:23:53,041] Trial 6 finished with value: 6.076874638649341 and parameters: {'learning_rate': 0.049415307858689174, 'num_leaves': 129, 'max_depth': 6, 'min_child_samples': 31, 'reg_alpha': 0.8612187887256694, 'reg_lambda': 8.774660381052438, 'colsample_bytree': 0.8804214947656988, 'n_estimators': 275}. Best is trial 3 with value: 4.2556751158162225.
[I 2025-02-24 21:23:53,066] Trial 7 finished with value: 8.80019683065152 and parameters: {'learning_rate': 0.12911436943963023, 'num_leaves': 101, 'max_depth': 12, 'min_child_samples': 37, 'reg_alpha': 5.534076137144701, 'reg_lambda': 5.658475194854468, 'colsample_byt

Best parameters for LightGBM: {'learning_rate': 0.28778546390768084, 'num_leaves': 140, 'max_depth': 9, 'min_child_samples': 22, 'reg_alpha': 0.5457990694020016, 'reg_lambda': 6.254372773894867, 'colsample_bytree': 0.9142614821421312, 'n_estimators': 425}
Tuning XGBoost...


[I 2025-02-24 21:37:44,985] Trial 0 finished with value: 4.4737960134045185 and parameters: {'n_estimators': 600, 'max_depth': 20, 'learning_rate': 0.0916239514050136, 'gamma': 1.3469227199511962, 'min_child_weight': 14, 'subsample': 0.5339591272128756, 'colsample_bytree': 0.8336986162056839, 'reg_alpha': 0.0001239784163700435, 'reg_lambda': 3.630055672898586}. Best is trial 0 with value: 4.4737960134045185.
[I 2025-02-24 21:37:45,472] Trial 1 finished with value: 6.586662151191292 and parameters: {'n_estimators': 550, 'max_depth': 16, 'learning_rate': 0.1643938145507321, 'gamma': 4.0977130639557044, 'min_child_weight': 7, 'subsample': 0.8754122924645449, 'colsample_bytree': 0.7770341229591797, 'reg_alpha': 0.010233613833114032, 'reg_lambda': 0.019290571898136478}. Best is trial 0 with value: 4.4737960134045185.
[I 2025-02-24 21:37:45,905] Trial 2 finished with value: 5.3607139540674416 and parameters: {'n_estimators': 575, 'max_depth': 18, 'learning_rate': 0.1421294454067177, 'gamma':

Best parameters for XGBoost: {'n_estimators': 575, 'max_depth': 17, 'learning_rate': 0.253190820895945, 'gamma': 2.735865024393669, 'min_child_weight': 19, 'subsample': 0.5895778398678168, 'colsample_bytree': 0.8083858673271751, 'reg_alpha': 0.0013008708215217712, 'reg_lambda': 0.9260168944510114}


# Test the model 

We test how good our ensemble would have predicted the outcome based on the last two years. 

In [ ]:
# ---------------------------
# 1. Load hyperparameters for each branch
# ---------------------------
with open("hyperparams_feb.json", "r") as f:
    hyperparams_feb = json.load(f)
# with open(hyperparams_march_file, "r") as f:
# hyperparams_march = json.load(f)

# ---------------------------
# 2. Prepare data and define target
# ---------------------------
df_training_prediction = df_training_dummies.copy()
df_training_prediction = df_training_prediction.dropna()
df_training_prediction = df_training_prediction[df_training_prediction['year']<2023]
y = df_training_prediction["bloom_doy"]

# ---------------------------
# 3. Define base models (common types for both branches)
# ---------------------------
base_models_dict = {
"SVR": SVR,
"BayesianRidge": BayesianRidge,
"LightGBM": lgb.LGBMRegressor,
"XGBoost": xgb.XGBRegressor
}

# ---------------------------
# 4. Build Feb ensemble
# ---------------------------


selected_features = feat_imp_df.head(191)['feature'].tolist()
X_feb = df_training_prediction[selected_features]
scaler_feb = StandardScaler()
X_feb_scaled = scaler_feb.fit_transform(X_feb)

base_models_feb = {}
predictions_list = []
for model_name, model_class in base_models_dict.items():
    params = hyperparams_feb.get(model_name, {})
    if model_name == "LightGBM":
        params["verbosity"] = -1

    model = model_class(**params)
    model.fit(X_feb_scaled, y)
    X_test_scaled = scaler_feb.transform(df_training_dummies[(df_training_dummies['year']>=2023)& (df_training_dummies['year']<=2024)][selected_features])
    prediction = model.predict(X_test_scaled)
    # print(model_name, prediction)
    predictions_list.append(prediction)
    rmse = (mean_absolute_error(df_training_dummies[(df_training_dummies['year']>=2023)& (df_training_dummies['year']<=2024)]['bloom_doy'], prediction))
    print(model_name, rmse)


ensemble_predictions = np.mean(np.vstack(predictions_list), axis=0)
# print(ensemble_predictions)
ensemble_mae = mean_absolute_error(df_training_dummies[(df_training_dummies['year']>=2023)& (df_training_dummies['year']<=2024)]['bloom_doy'], ensemble_predictions)


print(f"\nEnsemble Average Prediction MAE : {ensemble_mae:.2f}")
 



SVR 4.553268095989755
BayesianRidge 3.483573244369822
LightGBM 2.943721915516152
XGBoost 2.8952102661132812

Ensemble Average Prediction MAE : 2.84


# Preparing another scenario with information including march

In [10]:
def process_weather_data_with_advanced_features(folder_path):
    """
    Processes multiple weather CSV files and extracts key features for bloom prediction:
    - Growing Degree Days (GDD) from Jan to March
    - Warm Spell Days (>15°C in Feb-March)
    - Temperature Trend (Mean & Std Dev from Jan to March)
    - Temperature Variability (Nov–Jan)
    - Cold Days (<10°C)
    
    Args:
    folder_path (str): Path to the folder containing weather CSV files.

    Returns:
    pd.DataFrame: Concatenated DataFrame with processed weather data for all locations.
    """

    all_files = glob(os.path.join(folder_path, "*.csv"))
    processed_data = []

    for file in all_files:
        # Extract location name from filename
        location_name = os.path.basename(file).replace("_weather", "").replace("_", "/").replace(".csv", "")
        if location_name.lower() == "nyc":
            location_name = "newyorkcity"

        # Load and process weather data
        df_weather = pd.read_csv(file)
        df_weather["date"] = pd.to_datetime(df_weather["date"])

        # Extract year, month, and DOY
        df_weather["year"] = df_weather["date"].dt.year
        df_weather["month"] = df_weather["date"].dt.month
        df_weather["DOY"] = df_weather["date"].dt.dayofyear

        # Identify leap years
        df_weather["leap_year"] = df_weather["year"].apply(lambda x: 1 if (x % 4 == 0 and x % 100 != 0) or (x % 400 == 0) else 0)

        # Filter for relevant months (October to March)
        df_weather_filtered = df_weather[df_weather["month"].isin([10, 11, 12, 1, 2, 3])].copy()

        # Shift October-December to the next year for bloom alignment
        df_weather_filtered.loc[df_weather_filtered["month"].isin([10, 11, 12]), "year"] += 1

        # Compute daily averages
        df_daily_means = df_weather_filtered.groupby(["year", "DOY"]).agg({
            "temperature_2m_max": "mean",
            "temperature_2m_mean": "mean",
            "temperature_2m_min": "mean",
            "precipitation_sum": "mean",
            "rain_sum": "mean"
        }).reset_index()

        # Compute count of cold days separately
        df_cold_days = df_weather_filtered.groupby(["year", "DOY"])["temperature_2m_mean"].apply(lambda x: (x < 10).sum()).reset_index()
        df_cold_days.rename(columns={"temperature_2m_mean": "cold_days_below_10"}, inplace=True)

        # Compute temperature variability (std dev) for Nov-Jan per year-month
        df_temp_variability = df_weather_filtered[df_weather_filtered["month"].isin([11, 12, 1, 2, 3])].groupby(["year", "month"]).agg({
            "temperature_2m_mean": "std"
        }).reset_index().rename(columns={"temperature_2m_mean": "temp_variability"})

        # Feature 1: Growing Degree Days (GDD) - Base Temp 5°C (Jan-Mar)
        df_weather_filtered["GDD"] = df_weather_filtered["temperature_2m_mean"].apply(lambda x: max(0, x - 5))
        df_GDD = df_weather_filtered[df_weather_filtered["month"].isin([1, 2, 3])].groupby("year")["GDD"].sum().reset_index().rename(columns={"GDD": "total_GDD_Jan_Mar"})

        # Feature 2: Warm Spell Detection (Days > 15°C in Feb-March)
        df_weather_filtered["warm_spell_day"] = df_weather_filtered["temperature_2m_mean"] > 15
        df_warm_spells = df_weather_filtered[df_weather_filtered["month"].isin([1, 2, 3])].groupby("year")["warm_spell_day"].sum().reset_index().rename(columns={"warm_spell_day": "total_warm_spells_Feb_Mar"})

        # Feature 3: Temperature Trend (Mean & Std from Jan to March)
        temp_trend = df_weather_filtered[df_weather_filtered["month"].isin([1, 2, 3])].groupby("year").agg({"temperature_2m_mean": ["mean", "std"]})
        temp_trend.columns = ["temp_trend_mean", "temp_trend_std"]
        temp_trend.reset_index(inplace=True)

        # Merge cold day counts into daily means
        df_daily_means = df_daily_means.merge(df_cold_days, on=["year", "DOY"], how="left")

        # Ensure every (year, DOY) combination exists
        all_years = df_weather_filtered["year"].unique()
        valid_doys = df_weather_filtered["DOY"].unique()  # Only DOYs for Oct-Apr
        all_doys = sorted(valid_doys)  # Sort to maintain order

        full_doy_grid = pd.MultiIndex.from_product(
            [all_years, all_doys],
            names=["year", "DOY"]
        ).to_frame(index=False)

        # Merge to enforce a uniform structure
        df_daily_means_full = full_doy_grid.merge(df_daily_means, on=["year", "DOY"], how="left")

        # Fill missing values robustly
        df_daily_means_full.interpolate(method="linear", inplace=True)  # Fill using trends
        df_daily_means_full.fillna(df_daily_means_full.groupby("DOY").transform("median"), inplace=True)  # Use median where gaps exist
        df_daily_means_full.fillna(0, inplace=True)  # Ensure no NaNs remain

        # Add leap year column
        df_daily_means_full["leap_year"] = df_daily_means_full["year"].apply(lambda x: 1 if (x % 4 == 0 and x % 100 != 0) or (x % 400 == 0) else 0)

        # Pivot into a structured dataset (one row per year, columns per DOY)
        df_pivot_doy = df_daily_means_full.pivot(index="year", columns="DOY", values=["temperature_2m_max", "temperature_2m_mean", "temperature_2m_min", "precipitation_sum", "rain_sum", "cold_days_below_10"])

        # Flatten column names
        df_pivot_doy.columns = [f"{var}_DOY{doy}" for var, doy in df_pivot_doy.columns]

        # Reset index to keep "year" as a column
        df_pivot_doy.reset_index(inplace=True)

        # Add location column
        df_pivot_doy["location"] = location_name

        # Merge additional climate features
        df_additional_features = df_GDD.merge(df_warm_spells, on="year").merge(temp_trend, on="year")
        df_pivot_doy = df_pivot_doy.merge(df_additional_features, on="year", how="left")

        # Merge temperature variability per year-month into the dataset
        df_temp_variability_pivot = df_temp_variability.pivot(index="year", columns="month", values="temp_variability")
        df_temp_variability_pivot.columns = [f"temp_variability_M{month}" for month in df_temp_variability_pivot.columns]

        # Merge temperature variability into the final dataset
        df_pivot_doy = df_pivot_doy.merge(df_temp_variability_pivot, on="year", how="left")

        # Append to list
        processed_data.append(df_pivot_doy)

    # Concatenate all locations into a single dataframe
    final_df = pd.concat(processed_data, ignore_index=True)

    return final_df



processed_weather_data = process_weather_data_with_advanced_features("weather/")

In [11]:
# Ensure only necessary columns exist
df_training_march = df[['year', 'location', 'bloom_doy', 'alt', 'lat', 'long']].dropna()


# Convert year to numeric
df_training_march['year'] = pd.to_numeric(df_training_march['year'], errors='coerce')
df_training_march['year_squared'] = df_training_march['year'] ** 2
df_training_march['log_year'] = np.log(df_training_march['year'])
df_training_march['year_lat'] = df_training_march['year'] * df_training_march['lat']


# Sort data by location and year for< rolling calculations
df_training_march = df_training_march.sort_values(by=['location', 'year'])

# Compute rolling averages for bloom_doy within each location
df_training_march['bloom_doy_lag1'] = df_training_march.groupby('location')['bloom_doy'].shift(1)  # Last year's bloom day
df_training_march['bloom_doy_rolling2'] = df_training_march.groupby('location')['bloom_doy'].shift(1).rolling(window=2, min_periods=1).mean()
df_training_march['bloom_doy_rolling3'] = df_training_march.groupby('location')['bloom_doy'].shift(1).rolling(window=3, min_periods=1).mean()  
df_training_march['bloom_doy_rolling4'] = df_training_march.groupby('location')['bloom_doy'].shift(1).rolling(window=4, min_periods=1).mean()
df_training_march['bloom_doy_rolling5'] = df_training_march.groupby('location')['bloom_doy'].shift(1).rolling(window=5, min_periods=1).mean()  
df_training_march['bloom_doy_rolling7'] = df_training_march.groupby('location')['bloom_doy'].shift(1).rolling(window=7, min_periods=1).mean() 
df_training_march['bloom_doy_rolling10'] = df_training_march.groupby('location')['bloom_doy'].shift(1).rolling(window=10, min_periods=1).mean() 
df_training_march['alt_year'] = df_training_march['year']*df_training_march['alt']

df_training_march = df_training_march[df_training_march['year']>= 2000]


nyc_mask = (df_training_march['location'] == 'newyorkcity') & (df_training_march['year'] >= 2024)


df_training_march.loc[nyc_mask, 'bloom_doy_lag1'] = df_training_march.loc[nyc_mask, 'bloom_doy']


df_training_march.loc[nyc_mask, 'bloom_doy_rolling2'] =  df_training_march.loc[nyc_mask, 'bloom_doy']


df_training_march.loc[nyc_mask, 'bloom_doy_rolling3'] =  df_training_march.loc[nyc_mask, 'bloom_doy']

df_training_march.loc[nyc_mask, 'bloom_doy_rolling4'] =  df_training_march.loc[nyc_mask, 'bloom_doy']


df_training_march.loc[nyc_mask, 'bloom_doy_rolling5'] =  df_training_march.loc[nyc_mask, 'bloom_doy']


df_training_march.loc[nyc_mask, 'bloom_doy_rolling7'] = df_training_march.loc[nyc_mask, 'bloom_doy']


df_training_march.loc[nyc_mask, 'bloom_doy_rolling10'] =  df_training_march.loc[nyc_mask, 'bloom_doy']
# Merge the flower data with the weather data
df_training_march = df_training_march.merge(processed_weather_data, on=["year", "location"], how="left")

# Genearte the feature importance based on a LGBM model

In [ ]:
# 1. Prepare the data
# Create dummy variables for 'location' and filter for years < 2024
df_training_dummies_march = pd.get_dummies(df_training_march, columns=['location'], drop_first=True).dropna()

df_training_dummies_march['washington_year']= df_training_dummies_march['year']*df_training_dummies_march['log_year']

df_training_dummies_march_filtered = df_training_dummies_march[df_training_dummies_march['year'] < 2024].dropna()

# Separate features and target
X = df_training_dummies_march_filtered.drop(columns=['bloom_doy'])
y = df_training_dummies_march_filtered['bloom_doy']

# 2. Optionally, scale numerical features

scaler = StandardScaler()
X_scaled_arr = scaler.fit_transform(X)
# Convert back to DataFrame to retain column names
X_scaled = pd.DataFrame(X_scaled_arr, columns=X.columns, index=X.index)

# 3. Evaluate a LightGBM model using TimeSeriesSplit CV
tscv = TimeSeriesSplit(n_splits=3)
rmse_list = []

print("Evaluating LightGBM model with TimeSeriesSplit:")
for fold, (train_idx, test_idx) in enumerate(tscv.split(X_scaled), start=1):
    X_train, X_test = X_scaled.iloc[train_idx], X_scaled.iloc[test_idx]
    y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
    
    # Define and train the LightGBM regressor
    model = lgb.LGBMRegressor(random_state=42, verbosity = -1)
    model.fit(X_train, y_train,
              eval_set=[(X_test, y_test)])
    
    y_pred = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    rmse_list.append(rmse)
    print(f"Fold {fold} RMSE: {rmse:.2f}")

print(f"\nAverage RMSE from LightGBM (all features): {np.mean(rmse_list):.2f}\n")

# 4. Train a final LightGBM model on all training data to extract feature importances
final_model = lgb.LGBMRegressor(random_state=42, verbosity = -1)
final_model.fit(X_scaled, y)
feature_importances = final_model.feature_importances_


feat_imp_df_march = pd.DataFrame({'feature': X_scaled.columns, 'importance': feature_importances})
feat_imp_df_march = feat_imp_df_march.sort_values(by='importance', ascending=False)

# 5. Select top N features 
top_n = 128  # <-- Found trough trial and error 
selected_features_march = feat_imp_df_march.head(top_n)['feature'].tolist()

Evaluating LightGBM model with TimeSeriesSplit:
Fold 1 RMSE: 7.72
Fold 2 RMSE: 8.44
Fold 3 RMSE: 6.71

Average RMSE from LightGBM (all features): 7.63



# Model Tuning


In [ ]:
# def tune_model_with_optuna(model_name: str,
#                            X_train: np.ndarray, y_train: np.ndarray,
#                            X_test: np.ndarray, y_test: np.ndarray,
#                            n_trials: int = 50) -> dict:
#     """
#     Tune hyperparameters for a given model using Optuna with TimeSeriesSplit.
#     Returns the best hyperparameters.
#     """
#     def objective(trial: optuna.Trial) -> float:
#         if model_name == "SVR":
#             params = {
#                 "C": trial.suggest_float("C", 0.1, 1.0, log=True),
#                 "epsilon": trial.suggest_float("epsilon", 0.01, 1.0),
#                 "kernel": trial.suggest_categorical("kernel", ["linear"]),
#             }
#             model = SVR(**params)
            
#         elif model_name == "BayesianRidge":
#             params = {
#                 "alpha_1": trial.suggest_float("alpha_1", 1e-6, 1e-2, log=True),
#                 "alpha_2": trial.suggest_float("alpha_2", 1e-6, 1e-2, log=True),
#                 "lambda_1": trial.suggest_float("lambda_1", 1e-6, 1e-2, log=True),
#                 "lambda_2": trial.suggest_float("lambda_2", 1e-6, 1e-2, log=True),
#             }
#             model = BayesianRidge(**params)
            
#         elif model_name == "LightGBM":
#             params = {
#                 "objective": "regression",
#                 "metric": "rmse",
#                 "verbosity": -1,
#                 "boosting_type": "gbdt",
#                 "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
#                 "num_leaves": trial.suggest_int("num_leaves", 20, 150),
#                 "max_depth": trial.suggest_int("max_depth", 1, 20),
#                 "min_child_samples": trial.suggest_int("min_child_samples", 5, 50),
#                 "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 10),
#                 "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 10),
#                 "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0), 
#                 "n_estimators": trial.suggest_int("n_estimators", 50, 600, step=25)
#             }
#             model = lgb.LGBMRegressor(**params)
            
#         elif model_name == "XGBoost":
#             params = {
#                 "n_estimators": trial.suggest_int("n_estimators", 250, 600, step=25),
#                 "max_depth": trial.suggest_int("max_depth", 1, 20),
#                 "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
#                 "gamma": trial.suggest_float("gamma", 0, 5),
#                 "min_child_weight": trial.suggest_int("min_child_weight", 1, 30),
#                 "subsample": trial.suggest_float("subsample", 0.5, 0.9),
#                 "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 0.9),
#                 "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 10, log=True),
#                 "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 10, log=True)
#             }
#             model = xgb.XGBRegressor(**params)
#         else:
#             return float("inf")
        
#         # Train on the fixed training set and evaluate on the fixed test set.
#         model.fit(X_train, y_train)
#         y_pred = model.predict(X_test)
#         rmse = np.sqrt(np.mean((y_test - y_pred) ** 2))
#         return rmse

#     study = optuna.create_study(direction="minimize")
#     study.optimize(objective, n_trials=n_trials)
#     return study.best_params


# def tune_and_save_hyperparams(df_training: pd.DataFrame, selected_features: list, models_to_tune: list, n_trials: int = 50, save_path: str = "hyperparams_march.json") -> dict:
#     """
#     Tunes hyperparameters for each model in models_to_tune using time series cross-validation 
#     and saves them to a JSON file.
#     """
    
    
#     # Split the data based on the "year" column
#     train_df = df_training[df_training["year"] < 2023]
#     test_df = df_training[df_training["year"] >= 2023]
    
#     # Select features and target variable
#     X_train = train_df[selected_features]
#     y_train = train_df["bloom_doy"]
#     X_test = test_df[selected_features]
#     y_test = test_df["bloom_doy"]
    
#     # Fit the scaler on training data and transform both sets
#     scaler = StandardScaler()
#     X_train_scaled = scaler.fit_transform(X_train)
#     X_test_scaled = scaler.transform(X_test)
    
    
#     hyperparams = {}
#     for model_name in models_to_tune:
#         print(f"Tuning {model_name}...")
#         best_params = tune_model_with_optuna(model_name, X_train_scaled, y_train,
#                                              X_test_scaled, y_test, n_trials)
#         print(f"Best parameters for {model_name}: {best_params}")
#         hyperparams[model_name] = best_params

       

#     # Save the hyperparameters to a JSON file
    
#     with open(save_path, "w") as f:
#         json.dump(hyperparams, f)
#     return hyperparams


# # Example Usage:
# models_to_tune = ["SVR", "BayesianRidge", "LightGBM", "XGBoost"]

# # Assume df_training_dummies_filter is already defined and sorted by time
# # And 'selected_features' is a list of features you wish to use
# hyperparams = tune_and_save_hyperparams(df_training_dummies_march, selected_features_march, models_to_tune, n_trials=2500)

[I 2025-02-24 19:39:32,004] A new study created in memory with name: no-name-9de4f16c-3729-4ce8-aced-9eeefee99ee1
[I 2025-02-24 19:39:32,019] Trial 0 finished with value: 4.296255940994519 and parameters: {'C': 0.8359591880456504, 'epsilon': 0.9623672279931814, 'kernel': 'linear'}. Best is trial 0 with value: 4.296255940994519.
[I 2025-02-24 19:39:32,036] Trial 1 finished with value: 4.655792700269412 and parameters: {'C': 0.6149601354022355, 'epsilon': 0.6399141253283002, 'kernel': 'linear'}. Best is trial 0 with value: 4.296255940994519.
[I 2025-02-24 19:39:32,047] Trial 2 finished with value: 4.4989485948450625 and parameters: {'C': 0.3655954576414163, 'epsilon': 0.7367854006976146, 'kernel': 'linear'}. Best is trial 0 with value: 4.296255940994519.
[I 2025-02-24 19:39:32,058] Trial 3 finished with value: 4.760789412995483 and parameters: {'C': 0.2987486180638385, 'epsilon': 0.4944143123556875, 'kernel': 'linear'}. Best is trial 0 with value: 4.296255940994519.
[I 2025-02-24 19:39:3

Tuning SVR...


[I 2025-02-24 19:39:32,203] Trial 10 finished with value: 4.26777964704129 and parameters: {'C': 0.4766470908117847, 'epsilon': 0.9785541728145267, 'kernel': 'linear'}. Best is trial 4 with value: 4.223716923915475.
[I 2025-02-24 19:39:32,253] Trial 11 finished with value: 4.249198914359666 and parameters: {'C': 0.47212365001269524, 'epsilon': 0.9945803801948211, 'kernel': 'linear'}. Best is trial 4 with value: 4.223716923915475.
[I 2025-02-24 19:39:32,304] Trial 12 finished with value: 4.240279005845876 and parameters: {'C': 0.43143894064794064, 'epsilon': 0.9957318123786917, 'kernel': 'linear'}. Best is trial 4 with value: 4.223716923915475.
[I 2025-02-24 19:39:32,357] Trial 13 finished with value: 4.538520516309644 and parameters: {'C': 0.23224997795331567, 'epsilon': 0.8176607495241304, 'kernel': 'linear'}. Best is trial 4 with value: 4.223716923915475.
[I 2025-02-24 19:39:32,405] Trial 14 finished with value: 4.418887244205934 and parameters: {'C': 0.43716385948821246, 'epsilon': 

Best parameters for SVR: {'C': 0.2913442057169895, 'epsilon': 0.9999613148596452, 'kernel': 'linear'}
Tuning BayesianRidge...


[I 2025-02-24 19:42:15,265] Trial 4 finished with value: 4.161771067158001 and parameters: {'alpha_1': 1.1438511189193874e-06, 'alpha_2': 7.039196986793942e-06, 'lambda_1': 0.0006314313412569354, 'lambda_2': 3.180117562539938e-06}. Best is trial 0 with value: 4.161770991501496.
[I 2025-02-24 19:42:15,282] Trial 5 finished with value: 4.161768409823932 and parameters: {'alpha_1': 3.0806176837544976e-06, 'alpha_2': 0.0018367466305634962, 'lambda_1': 3.7834913618006653e-06, 'lambda_2': 1.0274885098990768e-05}. Best is trial 5 with value: 4.161768409823932.
[I 2025-02-24 19:42:15,299] Trial 6 finished with value: 4.161771929327077 and parameters: {'alpha_1': 2.0792632724765025e-06, 'alpha_2': 0.0011572730843531665, 'lambda_1': 1.7577490008544487e-05, 'lambda_2': 1.2385743191968363e-06}. Best is trial 5 with value: 4.161768409823932.
[I 2025-02-24 19:42:15,319] Trial 7 finished with value: 4.1619082991452245 and parameters: {'alpha_1': 0.0009515596128814331, 'alpha_2': 2.215798330591965e-06

Best parameters for BayesianRidge: {'alpha_1': 2.489497279026625e-06, 'alpha_2': 0.009974788413000878, 'lambda_1': 0.009942171868479704, 'lambda_2': 2.1741659278799076e-06}
Tuning LightGBM...


[I 2025-02-24 19:47:13,225] Trial 3 finished with value: 5.743245446311953 and parameters: {'learning_rate': 0.07095978429725845, 'num_leaves': 111, 'max_depth': 13, 'min_child_samples': 8, 'reg_alpha': 0.41445220866215987, 'reg_lambda': 8.7701552867804, 'colsample_bytree': 0.8843608448002902, 'n_estimators': 75}. Best is trial 2 with value: 5.626204391843539.
[I 2025-02-24 19:47:13,281] Trial 4 finished with value: 5.084290604618747 and parameters: {'learning_rate': 0.15362218880641135, 'num_leaves': 44, 'max_depth': 3, 'min_child_samples': 11, 'reg_alpha': 5.31558674990552, 'reg_lambda': 1.7885557816107776, 'colsample_bytree': 0.5625019187208538, 'n_estimators': 325}. Best is trial 4 with value: 5.084290604618747.
[I 2025-02-24 19:47:13,290] Trial 5 finished with value: 8.80019683065152 and parameters: {'learning_rate': 0.09528751749951478, 'num_leaves': 95, 'max_depth': 5, 'min_child_samples': 50, 'reg_alpha': 2.4738236619554232, 'reg_lambda': 4.749264538511703, 'colsample_bytree': 

Best parameters for LightGBM: {'learning_rate': 0.239186328272765, 'num_leaves': 28, 'max_depth': 18, 'min_child_samples': 29, 'reg_alpha': 2.7678974096203586, 'reg_lambda': 2.3266858963354218, 'colsample_bytree': 0.5176820580082253, 'n_estimators': 400}
Tuning XGBoost...


[I 2025-02-24 19:59:44,194] Trial 1 finished with value: 4.713903273228474 and parameters: {'n_estimators': 350, 'max_depth': 3, 'learning_rate': 0.08494725260414265, 'gamma': 0.3852217645070549, 'min_child_weight': 30, 'subsample': 0.8561934221261822, 'colsample_bytree': 0.5044828051775202, 'reg_alpha': 8.21621948092983, 'reg_lambda': 1.2398259058156098}. Best is trial 1 with value: 4.713903273228474.
[I 2025-02-24 19:59:44,489] Trial 2 finished with value: 5.332937033978926 and parameters: {'n_estimators': 550, 'max_depth': 12, 'learning_rate': 0.21840247423354828, 'gamma': 3.1133147619106727, 'min_child_weight': 9, 'subsample': 0.8142427126210018, 'colsample_bytree': 0.7648468585372389, 'reg_alpha': 0.07737901261417487, 'reg_lambda': 5.352636575603235}. Best is trial 1 with value: 4.713903273228474.
[I 2025-02-24 19:59:44,697] Trial 3 finished with value: 5.496565685386238 and parameters: {'n_estimators': 525, 'max_depth': 1, 'learning_rate': 0.11551207891343883, 'gamma': 3.40189803

Best parameters for XGBoost: {'n_estimators': 575, 'max_depth': 1, 'learning_rate': 0.22097162384932814, 'gamma': 3.9267467721200884, 'min_child_weight': 26, 'subsample': 0.7063934052165602, 'colsample_bytree': 0.8634617993190133, 'reg_alpha': 0.0028933506052396746, 'reg_lambda': 0.04206042758166962}


Check the predition accuracy for the years 2023 & 2024 

In [13]:
# ---------------------------
# 1. Load hyperparameters for each branch
# ---------------------------
with open("hyperparams_march.json", "r") as f:
    hyperparams_march = json.load(f)


# ---------------------------
# 2. Prepare data and define target
# ---------------------------
df_training_prediction = df_training_dummies_march.copy()
df_training_prediction = df_training_prediction.dropna()
df_training_prediction = df_training_prediction[df_training_prediction['year']<2023]
y = df_training_prediction["bloom_doy"]

# ---------------------------
# 3. Define base models (common types for both branches)
# ---------------------------
base_models_dict = {
"SVR": SVR,
"BayesianRidge": BayesianRidge,
"LightGBM": lgb.LGBMRegressor,
"XGBoost": xgb.XGBRegressor
}

# ---------------------------
# 4. Build Feb ensemble
# ---------------------------


selected_features_march = feat_imp_df_march.head(128)['feature'].tolist()
X_march= df_training_prediction[selected_features_march]
scaler_march = StandardScaler()
X_march_scaled = scaler_march.fit_transform(X_march)

base_models_feb = {}
predictions_list = []
for model_name, model_class in base_models_dict.items():
    params = hyperparams_march.get(model_name, {})
    if model_name == "LightGBM":
        params["verbosity"] = -1

    model = model_class(**params)
    model.fit(X_march_scaled, y)
    X_test_scaled = scaler_march.transform(df_training_dummies_march[(df_training_dummies_march['year']>=2023)& (df_training_dummies_march['year']<=2024)][selected_features_march])
    prediction = model.predict(X_test_scaled)
    # print(model_name, prediction)
    predictions_list.append(prediction)
    rmse = (mean_absolute_error(df_training_dummies_march[(df_training_dummies_march['year']>=2023)& (df_training_dummies_march['year']<=2024)]['bloom_doy'], prediction))
    print(model_name, rmse)


ensemble_predictions = np.mean(np.vstack(predictions_list), axis=0)
# print(ensemble_predictions)
ensemble_mae = mean_absolute_error(df_training_dummies_march[(df_training_dummies_march['year']>=2023)& (df_training_dummies_march['year']<=2024)]['bloom_doy'], ensemble_predictions)
print(f"\nEnsemble Average Prediction MAE : {ensemble_mae:.2f}")






SVR 2.6546735951382567
BayesianRidge 2.2520727304990453
LightGBM 3.0518329804367363
XGBoost 2.034310234917535

Ensemble Average Prediction MAE : 1.85


# Generate predictions for the year 2025 

In [ ]:
import json
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.base import clone
from sklearn.svm import SVR
from sklearn.linear_model import BayesianRidge
import lightgbm as lgb
import xgboost as xgb

def build_ensemble_and_predict_with_ci(
    df_training_feb: pd.DataFrame,
    df_training_march: pd.DataFrame,
    selected_features_feb: list,
    selected_features_march: list,
    hyperparams_feb_file: str = "hyperparams_feb.json",
    hyperparams_march_file: str = "hyperparams_march.json",
    n_bootstrap: int = 1000
) -> dict:
    """
    Trains two ensembles on all available training data using different feature sets:
      - The Feb branch uses features available until February.
      - The March branch uses features available until March.
    
    Both ensembles use their tuned hyperparameters (loaded from JSON files) and predict the target "bloom_doy"
    using a set of base models. The final prediction is simply the average of the predictions from both branches.
    
    Bootstrapping is performed to estimate a 90% confidence interval on the final averaged prediction.
    
    Parameters:
        df_training_feb (pd.DataFrame): Training dataset containing at least the target "bloom_doy", a "year" column,
                                    and a "location" column.
        df_training_march (pd.DataFrame): Training dataset containing at least the target "bloom_doy", a "year" column,
                                    and a "location" column.
        selected_features_feb (list): List of feature names available until February.
        selected_features_march (list): List of feature names available until March.
        hyperparams_feb_file (str): Path to the JSON file with tuned hyperparameters for the Feb base models.
        hyperparams_march_file (str): Path to the JSON file with tuned hyperparameters for the March base models.
        n_bootstrap (int): Number of bootstrap iterations for estimating prediction intervals.
    
    Returns:
        dict: Contains:
              - 'base_models_feb': dictionary of base models for February,
              - 'base_models_march': dictionary of base models for March,
              - 'scaler_feb' and 'scaler_march': scalers used for each branch,
              - 'case_study': a dict with final averaged predictions and their 90% CI for the next year's data.
              - hyperparameter dictionaries for reference.
    """
    # ---------------------------
    # 1. Load hyperparameters for each branch
    # ---------------------------
    with open(hyperparams_feb_file, "r") as f:
        hyperparams_feb = json.load(f)
    with open(hyperparams_march_file, "r") as f:
        hyperparams_march = json.load(f)
    
    # ---------------------------
    # 2. Prepare data and define target
    # ---------------------------
    df_training_prediction = df_training_feb.copy().dropna()
    df_training_prediction = df_training_prediction[df_training_prediction['year'] < 2025]
    y = df_training_prediction["bloom_doy"]
    
    # ---------------------------
    # 3. Define base models (common types for both branches)
    # ---------------------------
    base_models_dict = {
        "SVR": SVR,
        "BayesianRidge": BayesianRidge,
        "LightGBM": lgb.LGBMRegressor,
        "XGBoost": xgb.XGBRegressor
    }
    
    # ---------------------------
    # 4. Build Feb ensemble (without meta-model)
    # ---------------------------

    df_training_prediction = df_training_feb.copy().dropna()
    df_training_prediction = df_training_prediction[df_training_prediction['year'] < 2025]
    X_feb = df_training_prediction[selected_features_feb]

    scaler_feb = StandardScaler()
    X_feb_scaled = scaler_feb.fit_transform(X_feb)
    
    base_models_feb = {}
    for model_name, model_class in base_models_dict.items():
        params = hyperparams_feb.get(model_name, {})
        if model_name == "LightGBM":
            params["verbosity"] = -1
        model = model_class(**params)
        model.fit(X_feb_scaled, y)
        base_models_feb[model_name] = model
    
    # ---------------------------
    # 5. Build March ensemble (without meta-model)
    # ---------------------------
    df_training_prediction = df_training_march.copy().dropna()
    df_training_prediction = df_training_prediction[df_training_prediction['year'] < 2025]
    X_march = df_training_prediction[selected_features_march]
    scaler_march = StandardScaler()
    X_march_scaled = scaler_march.fit_transform(X_march)
    
    base_models_march = {}
    for model_name, model_class in base_models_dict.items():
        params = hyperparams_march.get(model_name, {})
        if model_name == "LightGBM":
            params["verbosity"] = -1
        model = model_class(**params)
        model.fit(X_march_scaled, y)
        base_models_march[model_name] = model
    
    # ---------------------------
    # 6. CASE STUDY: Predictions for Next Year (e.g., year 2025)
    # ---------------------------
    # 
    df_case_feb = df_training_feb[df_training_feb["year"] == 2025].copy().dropna()
    df_case_march = df_training_march[df_training_march["year"] == 2025].copy().dropna()
    # Prepare case features for Feb and March branches
    X_case_feb = scaler_feb.transform(df_case_feb[selected_features_feb])
    X_case_march = scaler_march.transform(df_case_march[selected_features_march])
    
    # Generate predictions from each base model and average for each branch
    preds_feb = np.column_stack([model.predict(X_case_feb) for model in base_models_feb.values()])
    ensemble_pred_feb = np.mean(preds_feb, axis=1)
    
    preds_march = np.column_stack([model.predict(X_case_march) for model in base_models_march.values()])
    ensemble_pred_march = np.mean(preds_march, axis=1)
    
    # Final prediction is the average of the Feb and March branch predictions
    y_case_pred = 0.5 * (ensemble_pred_feb + ensemble_pred_march)
    
    # ---------------------------
    # 7. Bootstrapping for 90% Confidence Intervals
    # ---------------------------
    boot_preds = []
    rng = np.random.RandomState(42)
    n_train_feb = X_feb_scaled.shape[0]
    n_train_march = X_march_scaled.shape[0]
    
    for _ in range(n_bootstrap):
        # Bootstrap sample for Feb branch
        indices_feb = rng.choice(n_train_feb, size=n_train_feb, replace=True)
        X_boot_feb = X_feb_scaled[indices_feb]
        y_boot_feb = y.iloc[indices_feb] if hasattr(y, "iloc") else y[indices_feb]
        boot_preds_feb = []
        for model_name, model in base_models_feb.items():
            model_boot = clone(model)
            model_boot.fit(X_boot_feb, y_boot_feb)
            boot_preds_feb.append(model_boot.predict(X_case_feb))
        ensemble_boot_feb = np.mean(np.column_stack(boot_preds_feb), axis=1)
        
        # Bootstrap sample for March branch
        indices_march = rng.choice(n_train_march, size=n_train_march, replace=True)
        X_boot_march = X_march_scaled[indices_march]
        y_boot_march = y.iloc[indices_march] if hasattr(y, "iloc") else y[indices_march]
        boot_preds_march = []
        for model_name, model in base_models_march.items():
            model_boot = clone(model)
            model_boot.fit(X_boot_march, y_boot_march)
            boot_preds_march.append(model_boot.predict(X_case_march))
        ensemble_boot_march = np.mean(np.column_stack(boot_preds_march), axis=1)
        
        # Combined bootstrap prediction: average of the two branch predictions
        combined_boot_pred = 0.5 * (ensemble_boot_feb + ensemble_boot_march)
        boot_preds.append(combined_boot_pred)
    
    boot_preds = np.array(boot_preds)  # shape: (n_bootstrap, n_case_samples)
    ci_lower = np.percentile(boot_preds, 5, axis=0)
    ci_upper = np.percentile(boot_preds, 95, axis=0)
    
    case_study_results = {
        "predictions": y_case_pred,
        "ci_lower": ci_lower,
        "ci_upper": ci_upper
    }
    
    return {
        "base_models_feb": base_models_feb,
        "base_models_march": base_models_march,
        "scaler_feb": scaler_feb,
        "scaler_march": scaler_march,
        "case_study": case_study_results,
        "hyperparams_feb": hyperparams_feb,
        "hyperparams_march": hyperparams_march
    }

# call:
results = build_ensemble_and_predict_with_ci(
    df_training_feb = df_training_dummies,
    df_training_march = df_training_dummies_march,
    selected_features_feb=selected_features,       # features for Feb branch
    selected_features_march=selected_features_march, # features for March branch
    hyperparams_feb_file="hyperparams_feb.json",
    hyperparams_march_file="hyperparams_feb.json"
)

print("Case Study Predictions:", results["case_study"]["predictions"])
print("90% CI Lower Bound:", results["case_study"]["ci_lower"])
print("90% CI Upper Bound:", results["case_study"]["ci_upper"])


Case Study Predictions: [95.82604244 86.15347961 92.38795661 91.58576761 87.01437711]
90% CI Lower Bound: [93.14084201 84.71396561 90.28071988 88.38543283 86.02603541]
90% CI Upper Bound: [96.8844883  88.48568545 94.27273127 92.99083411 90.00294289]


# Transform outcome into desired format

In [37]:
import csv


prediction_output  = pd.DataFrame({'location':df_training[df_training['year']==2025]['location'].values , 'prediction': np.round(results['case_study']['predictions']).astype(int), 
                                    'lower': np.round(results['case_study']['ci_lower']).astype(int), 'upper': np.round(results['case_study']['ci_upper']).astype(int)})

desired_order = ["washingtondc", "liestal", "kyoto", "vancouver", "newyorkcity"]

# Reorder the dataframe rows using the desired order
df_ordered = prediction_output.set_index("location").reindex(desired_order).reset_index()

df_ordered.to_csv('cherry-predictions.csv',index=False, quoting=csv.QUOTE_NONNUMERIC)


In [39]:
from datetime import datetime, timedelta

def doy_to_date(year, doy):
    # Subtract 1 because January 1st is day 1
    return datetime(year, 1, 1) + timedelta(days=doy - 1)

# Example:
year = 2025
df_ordered['date'] = pd.to_datetime(f"{year}-01-01") + pd.to_timedelta(df_ordered['prediction'] - 1, unit='d')
print(df_ordered)

       location  prediction  lower  upper       date
0  washingtondc          87     86     90 2025-03-28
1       liestal          86     85     88 2025-03-27
2         kyoto          96     93     97 2025-04-06
3     vancouver          92     88     93 2025-04-02
4   newyorkcity          92     90     94 2025-04-02
